In [20]:
import requests
import mysql.connector
from mysql.connector import Error
import schedule
import time


In [ ]:
# Airtable configuration
AIRTABLE_BASE_ID = 'appGnf8ldkBqyxsdX'
AIRTABLE_API_KEY = 'patb92KmkkX08CuWq.3e77882b6467bc2705d5f93a6468e7d74f8276494194126fe99328891d59f46b'
AIRTABLE_URL = f'https://api.airtable.com/v0/{AIRTABLE_BASE_ID}/'

# MySQL configuration
#MYSQL_HOST = 'ugandarugbyunion.cxuskymiehuv.eu-west-3.rds.amazonaws.com'
MYSQL_HOST = 'ugandarugbyunion.c5s2s2ki82x4.eu-north-1.rds.amazonaws.com'
MYSQL_DATABASE = 'ugandarugbyunion'
MYSQL_USER = 'admin' 
MYSQL_PASSWORD = '2210kpeteR$'

In [22]:
TABLE_NAMES = ['referees', 'prematchdata', 'postmatchdata', 'playerdata', 'circuitpoints7s', 'playerstats7s', 'penaltytry7s',
               'results7s','matches7s', 'injuries7s',
               'matches', 'ntplayers', 'schoollevelplayers', 'players',
               'teams', 'facilities', 'schoolteams', 'gircentres']

def fetch_airtable_records(table_name):
    url = AIRTABLE_URL + table_name
    headers = {
        'Authorization': f'Bearer {AIRTABLE_API_KEY}',
        'Content-Type': 'application/json'
    }
    response = requests.get(url, headers=headers)

    if response.status_code == 200:
        return response.json().get('records', [])
    else:
        print(f"❌ Failed to fetch records from {table_name}: {response.status_code}")
        return []

# Loop through all 10 tables
all_tables_data = {}

for table in TABLE_NAMES:
    records = fetch_airtable_records(table)
    all_tables_data[table] = records
    print(f"✅ {table}: {len(records)} records fetched.")



✅ referees: 49 records fetched.
✅ prematchdata: 6 records fetched.
✅ postmatchdata: 100 records fetched.
✅ playerdata: 12 records fetched.
✅ circuitpoints7s: 12 records fetched.
✅ playerstats7s: 36 records fetched.
✅ penaltytry7s: 9 records fetched.
✅ results7s: 30 records fetched.
✅ matches7s: 30 records fetched.
✅ injuries7s: 12 records fetched.
✅ matches: 36 records fetched.
✅ ntplayers: 35 records fetched.
✅ schoollevelplayers: 100 records fetched.
✅ players: 100 records fetched.
✅ teams: 92 records fetched.
✅ facilities: 14 records fetched.
✅ schoolteams: 97 records fetched.
✅ gircentres: 100 records fetched.


In [23]:
gir_records = fetch_airtable_records('gircentres')  # Specify the table name
print(gir_records)


[{'id': 'rec0Z6yJ6B2jIOt8T', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'Central ', 'GIRCenter': 'Kireka', 'GIRName': 'Don Bosco', 'PitchStatus': 'Active'}}, {'id': 'rec0lkaKPZBoVXCZY', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'Central ', 'GIRCenter': 'Nsambya', 'GIRName': 'Kibuli Police ', 'PitchStatus': 'Active'}}, {'id': 'rec15L6kneP6Noc4J', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'North', 'GIRCenter': 'Omoro', 'GIRName': 'Lapinyologo', 'PitchStatus': 'Active'}}, {'id': 'rec1TGPYKDlTqF6GW', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'East ', 'GIRCenter': 'Mbale', 'GIRName': 'Wambwa Center', 'PitchStatus': 'Active'}}, {'id': 'rec2Cw1XiGDnmyfcq', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'North', 'GIRCenter': 'Lira', 'GIRName': 'Northern Force', 'PitchStatus': 'Active'}}, {'id': 'rec32zECTzDObLfSF', 'createdTime': '2025-04-09T15:37:40.000Z', 'fields': {'Region': 'North', 'GIR

In [ ]:
def upsert_record(cursor, table, record):
    fields = record.get('fields', {})

    if table == 'referees':
        sql = """
        INSERT INTO referees (RefName, Status)
        VALUES (%s, %s)
        ON DUPLICATE KEY UPDATE 
            Status = VALUES(Status);
        """

        values = (
            fields.get('RefName'), 
            fields.get('Status')
        )
   
    elif table == 'prematchdata':
        sql = """
        INSERT INTO prematchdata (
            Dates, Game, Venue, Category, Times,
            CentreReferee, AR1, AR2, Assessor, Citing, MC
        ) VALUES (
            %s, %s, %s, %s, %s,
            %s, %s, %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Venue = VALUES(Venue),
            Category = VALUES(Category),
            Times = VALUES(Times),
            CentreReferee = VALUES(CentreReferee),
            AR1 = VALUES(AR1),
            AR2 = VALUES(AR2),
            Assessor = VALUES(Assessor),
            Citing = VALUES(Citing),
            MC = VALUES(MC);
        """
        
        values = (
            fields.get('Dates'),
            fields.get('Game'),
            fields.get('Venue'),
            fields.get('Category'),
            fields.get('Times') or '',
            fields.get('CentreReferee'),
            fields.get('AR1') or '',
            fields.get('AR2') or '',
            fields.get('Assessor') or '',
            fields.get('Citing') or '',
            fields.get('MC') or ''
        )

        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'postmatchdata':
        sql = """
        INSERT INTO postmatchdata (
            DateColumn, Club, PlayerName, Tries, Conversions, ConversionsMissed,
            Penalties, PenaltiesMissed, DropGoals, DropGoalsMissed,
            PenaltyTry, TotalPoints, YellowCards, RedCards, SeriousInjuriesSustained
        ) VALUES (
            %s, %s, %s, %s, %s, %s,
            %s, %s, %s, %s,
            %s, %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Tries = VALUES(Tries),
            Conversions = VALUES(Conversions),
            ConversionsMissed = VALUES(ConversionsMissed),
            Penalties = VALUES(Penalties),
            PenaltiesMissed = VALUES(PenaltiesMissed),
            DropGoals = VALUES(DropGoals),
            DropGoalsMissed = VALUES(DropGoalsMissed),
            PenaltyTry = VALUES(PenaltyTry),
            TotalPoints = VALUES(TotalPoints),
            YellowCards = VALUES(YellowCards),
            RedCards = VALUES(RedCards),
            SeriousInjuriesSustained = VALUES(SeriousInjuriesSustained);
        """
            # Get the Club field from Airtable
        club_field = fields.get('Club')


        values = (
            fields.get('DateColumn'),
            club_field or 0,
            fields.get('PlayerName'),
            fields.get('Tries') or 0,
            fields.get('Conversions') or 0,
            fields.get('ConversionsMissed') or 0,
            fields.get('Penalties') or 0,
            fields.get('PenaltiesMissed') or 0,
            fields.get('DropGoals') or 0,
            fields.get('DropGoalsMissed') or 0,
            fields.get('PenaltyTry') or 0,
            fields.get('TotalPoints') or 0,
            fields.get('YellowCards') or 0,
            fields.get('RedCards') or 0,
            fields.get('SeriousInjuriesSustained') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'matches':
        sql = """
        INSERT INTO matches (
            MatchDate, 
            HomeTeam, AwayTeam, HomePoints, AwayPoints,
            HomeTries, AwayTries, Result
        ) VALUES (
            %s, %s, %s, %s, %s,
            %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            HomePoints = VALUES(HomePoints),
            AwayPoints = VALUES(AwayPoints),
            HomeTries = VALUES(HomeTries),
            AwayTries = VALUES(AwayTries),
            Result = VALUES(Result);
        """

        values = (
            fields.get('MatchDate') or '',
            fields.get('HomeTeam') or '',
            fields.get('AwayTeam') or '',
            fields.get('HomePoints') or '',
            fields.get('AwayPoints') or '',
            fields.get('HomeTries') or '',
            fields.get('AwayTries') or '',
            fields.get('Result') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'ntplayers':
        sql = """
        INSERT INTO ntplayers (PlayerName, DOB, Club, Status, NTParticipation, NTLevel, U19, NTCaps, Gender)
        VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE 
            Club = VALUES(Club),
            Status = VALUES(Status), 
            NTParticipation = VALUES(NTParticipation), 
            NTLevel = VALUES(NTLevel), 
            U19 = VALUES(U19), 
            NTCaps = VALUES(NTCaps),
            Gender = VALUES(Gender);
        """
            # Get the Club field from Airtable
        club_field = fields.get('Club')

        values = (
            fields.get('PlayerName'), 
            fields.get('DOB'),  # Ensure this is in the correct date format
            club_field or 0, 
            fields.get('Status'), 
            fields.get('NTParticipation') or '', 
            fields.get('NTLevel'), 
            fields.get('U19') or '', 
            fields.get('NTCaps'),
            fields.get('Gender') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'schoollevelplayers':
        sql = """
        INSERT INTO schoollevelplayers (PlayerName, DOB, School, StartDate, AgeCategory, Status, Gender, Club, U19)
        VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE
        
            StartDate = VALUES(StartDate),
            AgeCategory = VALUES(AgeCategory),
            Status = VALUES(Status),
            Gender = VALUES(Gender),
            Club = VALUES(Club),
            U19 = VALUES(U19);
        """
            # Get the Club field from Airtable
        club_field = fields.get('Club')

        # Check if Club is None and set it to 0
        if club_field is None:
            club_field = 0  # Assign 0 if the club is missing

        values = (
            fields.get('PlayerName'), 
            fields.get('DOB') or '',  # Ensure DOB is in the correct format
            fields.get('School'), 
            fields.get('StartDate') or '', 
            fields.get('AgeCategory') or '',
            fields.get('Status') or '',
            fields.get('Gender') or '', 
            club_field, 
            fields.get('U19') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'players':
        sql = """
        INSERT INTO players (Club, PlayerName, DOB, Status, PlayerImage, Years, Gender)
        VALUES (%s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE 
            Status = VALUES(Status),
            PlayerImage = VALUES(PlayerImage),
            Years = VALUES(Years),
            Gender = VALUES(Gender);
        """
            # Get the Club field from Airtable
        club_field = fields.get('Club')

        values = (
            club_field or 0, 
            fields.get('PlayerName'), 
            fields.get('DOB') or '',  # Ensure date is in the correct format
            fields.get('Status'), 
            fields.get('PlayerImage') or 0,
            fields.get('Years'),
            fields.get('Gender') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'teams':
        sql = """
        INSERT INTO teams (Team, City, Stadium, Region, Gender)
        VALUES (%s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE
        City = VALUES(City),
        Stadium = VALUES(Stadium),
        Region = VALUES(Region),
        Gender = VALUES(Gender);
        """

        values = (
            fields.get('Team'),  
            fields.get('City') or '', 
            fields.get('Stadium') or '', 
            fields.get('Region') or '', 
            fields.get('Gender') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'facilities':
        sql = """
        INSERT INTO facilities (Facility, Region, District)
        VALUES (%s, %s, %s)
        ON DUPLICATE KEY UPDATE 
        Region = VALUES(Region),
        District = VALUES(District);
        """

        values = (
            fields.get('Facility'), 
            fields.get('Region') or '', 
            fields.get('District') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'schoolteams':
        sql = """
        INSERT INTO schoolteams (Region, School, Gender)
        VALUES (%s, %s, %s)
        ON DUPLICATE KEY UPDATE 
        Region = VALUES(Region),
        Gender = VALUES(Gender);
        """

        values = (
            fields.get('Region'),  
            fields.get('School'), 
            fields.get('Gender')
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging

        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'gircentres':
        sql = """
        INSERT INTO gircentres (Region, GIRCenter, GIRName, PersonInCharge, Phone, PitchStatus, Try, Play, Stay)
        VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE 
        Region = VALUES(Region),
        GIRCenter = VALUES(GIRCenter),
        PersonInCharge = VALUES(PersonInCharge),
        Phone = VALUES(Phone),
        PitchStatus = VALUES(PitchStatus),
        Try = VALUES(Try),
        Play = VALUES(Play),
        Stay = VALUES(Stay);
        """

        values = (
            fields.get('Region'),        
            fields.get('GIRCenter') or '', 
            fields.get('GIRName'),  
            fields.get('PersonInCharge') or '', 
            fields.get('Phone') or '', 
            fields.get('PitchStatus'),
            fields.get('Try') or '', 
            fields.get('Play') or '', 
            fields.get('Stay') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")  # Logging
    elif table == 'circuitpoints7s':
        sql = """
        INSERT INTO circuitpoints7s (
            Team, Points, Circuit
        ) VALUES (
            %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Points = VALUES(Points);
        """

        values = (
            fields.get('Team') or '',
            fields.get('Points') or 0,
            fields.get('Circuit') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")
    elif table == 'resultcolours':
        sql = """
        INSERT INTO resultcolours (
            Result, ResultColour
        ) VALUES (
            %s, %s
        )
        ON DUPLICATE KEY UPDATE
            ResultColour = VALUES(ResultColour);
        """

        values = (
            fields.get('Result'),
            fields.get('ResultColour'),
            
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")
    
    elif table == 'playerstats7s':
        sql = """
        INSERT INTO playerstats7s (
            Circuit, PlayerName, Club, Tries, Conversions,
            Penalties, YellowCards, RedCards, DropGoals
        ) VALUES (
            %s, %s, %s, %s, %s,
            %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Tries = VALUES(Tries),
            Conversions = VALUES(Conversions),
            Penalties = VALUES(Penalties),
            YellowCards = VALUES(YellowCards),
            RedCards = VALUES(RedCards),
            DropGoals = VALUES(DropGoals);
        """

        values = (
            fields.get('Circuit') or '',
            fields.get('PlayerName') or '',
            fields.get('Club') or '',
            fields.get('Tries') or 0,
            fields.get('Conversions') or 0,
            fields.get('Penalties') or 0,
            fields.get('YellowCards') or 0,
            fields.get('RedCards') or 0,
            fields.get('DropGoals') or 0
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")


    elif table == 'penaltytry7s':
        sql = """
        INSERT INTO penaltytry7s (
            Club, MatchID, PenaltyTry
        ) VALUES (
            %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            PenaltyTry = VALUES(PenaltyTry);
        """

        values = (
            fields.get('Club') or '',
            fields.get('MatchID') or '',
            fields.get('PenaltyTry') or 0
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'results7s':
        sql = """
        INSERT INTO results7s (
            MatchID, Date, HomeTeam, AwayTeam,
            HomePoints, AwayPoints, HomeTries, AwayTries, Result
        ) VALUES (
            %s, %s, %s, %s, %s, %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            HomePoints = VALUES(HomePoints),
            AwayPoints = VALUES(AwayPoints),
            HomeTries = VALUES(HomeTries),
            AwayTries = VALUES(AwayTries),
            Result = VALUES(Result);
        """

        values = (
            fields.get('MatchID') or '',
            fields.get('Date') or '',
            fields.get('HomeTeam') or '',
            fields.get('AwayTeam') or '',
            fields.get('HomePoints') or 0,
            fields.get('AwayPoints') or 0,
            fields.get('HomeTries') or 0,
            fields.get('AwayTries') or 0,
            fields.get('Result') or 0
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'matches7s':
        sql = """
        INSERT INTO matches7s (
            MatchID, Dates, HomeTeam, AwayTeam, Circuit, Venue, Referee
        ) VALUES (
            %s, %s, %s, %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Dates = VALUES(Dates),
            Circuit = VALUES(Circuit),
            Venue = VALUES(Venue),
            Referee = VALUES(Referee);
        """

        values = (
            fields.get('MatchID') or '',
            fields.get('Dates') or '',
            fields.get('HomeTeam') or '',
            fields.get('AwayTeam') or '',
            fields.get('Circuit') or '',
            fields.get('Venue') or '',
            fields.get('Referee') or ''
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")

    elif table == 'injuries7s':
        sql = """
        INSERT INTO injuries7s (
            Dates, Venue, Circuit, Club, PlayerName, SeriousInjuriesSustained
        ) VALUES (
            %s, %s, %s, %s, %s, %s
        )
        ON DUPLICATE KEY UPDATE
            Venue = VALUES(Venue),
            Club = VALUES(Club),
            PlayerName = VALUES(PlayerName),
            SeriousInjuriesSustained = VALUES(SeriousInjuriesSustained);
        """

        values = (
            fields.get('Dates') or '',
            fields.get('Venue') or '',
            fields.get('Circuit') or '',
            fields.get('Club') or '',
            fields.get('PlayerName') or '',
            fields.get('SeriousInjuriesSustained') or 0
        )
        print(f"Executing SQL: {sql} with values: {values}")
        try:
            cursor.execute(sql, values)
        except Error as err:
            print(f"Error executing SQL for table {table}: {err}")


    else:
        print(f"⚠️ Table '{table}' not handled.")
        return

    try:
        cursor.execute(sql, values)
    except Error as err:
        print(f"Error executing SQL for table {table}: {err}")


In [ ]:
# Main function to synchronize Airtable with MySQL
def sync_airtable_to_mysql():
    try:
        connection = mysql.connector.connect(
            host=MYSQL_HOST,
            database=MYSQL_DATABASE,
            user=MYSQL_USER,
            password=MYSQL_PASSWORD
        )
        
        if connection.is_connected():
            cursor = connection.cursor()

            # List of tables to synchronize along with their primary keys (either single or composite)
            tables = {
                'referees': ['RefName'],  # Composite primary key or two unique keys combined
                #'playerdata': ['Club'], # Single primary key
                'players': ['PlayerName', 'Club'],  # Single primary key
                'schoolteams': ['School'],  # Single primary key
                'gircentres': ['GIRName'],  # Single primary key
                'teams': ['Team'],  # Single primary key
                'schoollevelplayers': ['PlayerName', 'DOB', 'School'],  # Composite primary key
                'prematchdata': ['Dates', 'Game'],  # Composite primary key
                'postmatchdata': ['DateColumn', 'PlayerName', 'Club'],  # Composite primary key
                'matches': ['MatchDate', 'HomeTeam', 'AwayTeam'],  # Composite primary key
                'ntplayers': ['PlayerName', 'DOB'],  # Composite primary key
                'facilities': ['Facility'],  # Single primary key
                'injuries7s': ['Dates','Circuit'],
                'resultcolours': ['Result'],
                'matches7s': ['MatchID','HomeTeam', 'AwayTeam'],
                'results7s': ['MatchID', 'HomeTeam', 'AwayTeam'],
                'penaltytry7s': ['Club','MatchID'],
                'playerstats7s': ['Circuit', 'PlayerName', 'Club'],
                'circuitpoints7s': ['Circuit', 'Team']
            }

            for table, primary_keys in tables.items():
                # Construct SQL SELECT statement using primary keys
                primary_key_clause = " AND ".join(f"{key} = %s" for key in primary_keys)
                
                # Create SQL to fetch existing records
                select_sql = f"SELECT {', '.join(primary_keys)} FROM {table};"
                cursor.execute(select_sql)
                existing_records = {tuple(row) for row in cursor.fetchall()}  # Set of tuples

                # Fetch records from Airtable
                records = fetch_airtable_records(table)  # Specify table name
                
                # Prepare to track fetched records from Airtable
                fetched_identifiers = set()

                for record in records:
                    identifier = tuple(record['fields'].get(key) for key in primary_keys)  # Create a tuple for identifiers
                    upsert_record(cursor, table, record)  # Call the upsert function

                    # Track fetched identifiers
                    fetched_identifiers.add(identifier)

                # Deletions: Identify records in MySQL not found in Airtable
                for identifier in existing_records:
                    if identifier not in fetched_identifiers:
                        # Create delete SQL statement
                        delete_sql = f"DELETE FROM {table} WHERE {primary_key_clause};"
                        cursor.execute(delete_sql, tuple(identifier))  # Explicitly convert identifier to a tuple

            connection.commit()  # Commit all changes
            print("Data synchronized successfully, including deletions.")

    except mysql.connector.Error as e:
        print(f"Error while connecting to MySQL: {e}")
        connection.rollback()
    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()

# Schedule the sync function to run every minute
schedule.every(1).minutes.do(sync_airtable_to_mysql)

# Keep the script running to maintain the scheduling
while True:
    schedule.run_pending()
    time.sleep(1)  # Sleep to prevent high CPU usage


Executing SQL: 
        INSERT INTO players (Club, PlayerName, DOB, Status, PlayerImage, Years, Gender)
        VALUES (%s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE 
            Status = VALUES(Status),
            PlayerImage = VALUES(PlayerImage),
            Years = VALUES(Years),
            Gender = VALUES(Gender);
         with values: ('Kobs ', 'Adnan Mutebi', '1992-01-04', 'Active', '0', '2025', 'Male')
Executing SQL: 
        INSERT INTO players (Club, PlayerName, DOB, Status, PlayerImage, Years, Gender)
        VALUES (%s, %s, %s, %s, %s, %s, %s)
        ON DUPLICATE KEY UPDATE 
            Status = VALUES(Status),
            PlayerImage = VALUES(PlayerImage),
            Years = VALUES(Years),
            Gender = VALUES(Gender);
         with values: ('Pirates ', 'Raphael Anyama', '1996-06-08', 'Active', '0', '2025', 'Male')
Executing SQL: 
        INSERT INTO players (Club, PlayerName, DOB, Status, PlayerImage, Years, Gender)
        VALUES (%s, %s, %s, %s,

MySQLInterfaceError: Lost connection to MySQL server during query